In [1]:
"""Create parameters.py from a .inp and load it"""
# This cell is facultative, you can use an existing parameters.py

# Directory for .inp file:
path = 'Bubble_dynamics_simulation/INP file examples/chem_Otomo2018_without_O.inp'

# import libraries:
import importlib   # for reloading your own files
from termcolor import colored   # for colored error messages
# my own files:
try:
    import inp_data_extractor as inp
except:
    try:
        import Bubble_dynamics_simulation.inp_data_extractor as inp
    except:
        print(colored(f'Error, \'inp_data_extractor.py\' not found', 'red'))
importlib.reload(inp)

# create parameters.py
inp.extract(path)

# load parameters.py
import parameters as par
importlib.reload(par)
print(par.model)

path=Bubble_dynamics_simulation/INP file examples/chem_Otomo2018_without_O.inp
Note, lambda value for specie 'H' is not in data.py: 0.0 is used
Note, lambda value for specie 'NH2' is not in data.py: 0.0 is used
Note, lambda value for specie 'NH' is not in data.py: 0.0 is used
Note, lambda value for specie 'N' is not in data.py: 0.0 is used
Note, lambda value for specie 'NNH' is not in data.py: 0.0 is used
Note, lambda value for specie 'N2H4' is not in data.py: 0.0 is used
Note, lambda value for specie 'N2H3' is not in data.py: 0.0 is used
Note, lambda value for specie 'N2H2' is not in data.py: 0.0 is used
Note, lambda value for specie 'H2NN' is not in data.py: 0.0 is used
Warning, third body 'H2O' is not in species in line 64 (' H2/2.5/ H2O/12/ AR/0.0/ ') in reaction 'H2+M=H+H+M'
Warning, third body 'AR' is not in species in line 64 (' H2/2.5/ H2O/12/ AR/0.0/ ') in reaction 'H2+M=H+H+M'
model: chem_Otomo2018_without_O
File 'parameters.py' succesfully created
chem_Otomo2018_without_O


In [2]:
"""Libraries"""

# for plotting:
%matplotlib inline
import matplotlib.pyplot as plt
plt.rcParams.update({'font.size': 18})

import numpy as np   # matrices, math
import time   # runtime measurement
from multiprocessing import Pool, cpu_count   # multithreading
import importlib   # reload changes you made
import itertools   # assemble all combinations of control parameters
import json   # convert dictionary to string

# my own file:
already_imported = 'de' in globals()
try:
    import full_bubble_model as de
except:
    try:
        import Bubble_dynamics_simulation.full_bubble_model as de
    except:
        print(colored(f'Error, \'full_bubble_model.py\' not found', 'red'))
if already_imported: importlib.reload(de)   # reload changes you made

model: chem_Otomo2018_without_O
target specie: NH3
excitation: sin_impulse (control parameters: ['p_A', 'freq', 'n'])
enable heat transfer: True	enable evaporation: False	enable reactions: True	enable dissipated energy: True


In [4]:
"""Control parameter ranges and division"""
# a list for each control parameter, containing all the possible values

ranges = dict(
  # Initial conditions:
    # bubble equilibrium radius [m]
    R_E = [1e-6*x for x in [1.0, 2.0, 3.0, 4.0, 5.0, 7.5, 10.0, 15.0, 20.0, 25.0]], # [um --> m]
    # initial radius / equilibrium radius R_0/R_E [-]
    ratio = [1.0],
  # Ambient parameters:
    # ambient pressure [Pa]
    P_amb = [x * par.atm2Pa for x in [0.25, 0.5, 0.75, 1.0, 1.5, 2.0, 5.0]], # [atm --> Pa]
    # ambient temperature [K]       
    T_inf = [par.absolute_zero + x for x in [30.0]], # [°C --> K]
  # Liquid parameters:
    # water accommodation coefficient [-]
    alfa_M = [0.05, 0.35],
    #P_v = par.P_v,                    # vapour pressure [Pa]
    #mu_L = par.mu_L,                  # dynamic viscosity [Pa*s]
    # sound speed [m/s]
    c_L = [par.c_L],
    # surfactant (surface tension modfier) [-]
    surfactant = [1.0],
  # Excitation parameters: (excitation_type = no_excitation)
    # pressure amplitude [Pa]
    p_A = [-x * 1e5 for x in [0.5, 1.0, 1.5, 2.0, 2.5, 3.0, 5.0]], # [bar --> Pa]
    # frequency [Hz]
    freq = [1.0e3, 5.0e3, 10.0e3, 20.0e3, 30.0e3, 40.0e3, 50.0e3, 100.0e3],
    # number of cycles [-]
    n = [0.5, 1.0, 2.0],
)

# print total combinations:
for key in ranges:
    print(f'{key}: {len(ranges[key])}')
total_combinations = f'total combinations: {np.prod([len(ranges[key]) for key in ranges])}'
print(''.join(['_' for i in range(len(total_combinations))]))
print(total_combinations)

R_E: 10
ratio: 1
P_amb: 7
T_inf: 1
alfa_M: 2
c_L: 1
surfactant: 1
p_A: 7
freq: 8
n: 3
_________________________
total combinations: 23520


In [5]:
"""Get all combinations"""
# Make a list, with one dictionary for eachy parameter combinations

start = time.time()
cpars = []
ID = 1
for values in itertools.product(*ranges.values()):
    cpar = dict(zip(ranges.keys(), values))
    cpar['ID'] = ID                      # ID of control parameter (not used during calculation)
    cpar['gases'] = [par.index['H2'], par.index['N2']]    # indexes of species in initial bubble (list of species indexes)
    cpar['fractions'] = [0.75, 0.25]            # molar fractions of species in initial bubble (list of fractions for every gas)
    # Calculate pressure/temperature dependent parameters:
    cpar['mu_L'] = de.Viscosity(cpar['T_inf'])
    cpar['P_v'] = de.VapourPressure(cpar['T_inf'])
    cpars.append(cpar)
    ID += 1

print(f'Assemble cpars: {time.time()-start:.2f} s')
start = time.time()

# Create input dictionary for de.simulate(), a list of dictionaries with cpar and other arguments
kwargs_list = [dict(cpar=cpar, t_int=np.array([0.0, 1.0]), LSODA_timeout=100, Radau_timeout=300) for cpar in cpars]
end = time.time()
print(f'Assemble kwargs_list: {time.time()-start:.2f} s')

Assemble cpars: 0.12 s
Assemble kwargs_list: 0.24 s


In [6]:
"""Save settings as txt"""

# create folder for parameter study results:
file = de.Make_dir('first_search_better_settings')

# save all settings (full_bubble_model.py, parameters.py, ranges) as txt:
combined_str = f'''parameters settings:
    model = {par.model}
    species = {par.species}
    number of species = {par.K}
    number of reactions = {par.I}

full_bubble_model settings:
    enable_heat_transfer = {de.enable_heat_transfer}
    enable_evaporation = {de.enable_evaporation} 
    enable_reactions = {de.enable_reactions}
    enable_dissipated_energy = {de.enable_dissipated_energy}
    target_specie = \'{de.target_specie}\' # Specie to calculate energy effiqiency
    excitation_type = \'{de.excitation_type}\' # function to calculate pressure excitation

total_combinations = {np.prod([len(ranges[key]) for key in ranges])}
ranges = {json.dumps(ranges, indent=4)}'''

file.write_string(combined_str, 'brutefroce_parameter_sweep_settings')

In [8]:
"""Parameter study, multithread"""
# Runs each combinations in cpars, and saves the results into CSV files
# use Pool(processes=cpu_count()-1) to limit number of threads being used.
# use pool.imap(...) instead of pool.imap_unordered(...) to preserve order in which cpars was made

max_lines = 2000    # maximum length of a CSV
best_energy_efficiency = 1e30

start = time.time()
file.new_file()
with Pool(processes=cpu_count(), maxtasksperchild=100) as pool:
    results = pool.imap_unordered(de.simulate, kwargs_list)

    for data in results:
      # save results:
        if file.lines > max_lines:
            file.close()
            file.new_file()
        data = de.dotdict(data)
        file.write_line(data)
      # print stuff:
        if data.energy_efficiency > 0 and data.energy_efficiency < best_energy_efficiency:
            best_energy_efficiency = data.energy_efficiency
        print(f'index: {data.ID}/{len(cpars)},   error_code: {data.error_code: >4},   steps: {data.steps},   runtime: {data.elapsed_time: .2f} [s]   |   '+
              f'R_E={1e6*data.R_E: .2f} [um]; ratio={data.ratio: .2f} [-]; P_amb={1e-5*data.P_amb: .2f} [bar]; alfa_M={data.alfa_M: .2f} [-]; '+
              f'T_inf={data.T_inf-273.15: .2f} [°C]; surfactant={100*data.surfactant: .0f} [%]   |   {de.target_specie} production: {data.energy_efficiency: .1f} [MJ/kg] '+
              f'(best: {best_energy_efficiency: .1f} [MJ/kg])                                                 ', end='\r')
            
file.close()
end = time.time()
elapsed = end - start
print(f'\n\nDONE')
print(f'total time: {(elapsed / 3600): .0f} hours {((elapsed % 3600) / 60): .0f} mins')
print(f'            {elapsed: .2f} [s]   ({(elapsed / len(    cpars)): .2f} [s/run])')

 lsoda--  warning..internal t (=r1) and h (=r2) are   runtime:  3.21 [s]   |   R_E= 1.00 [um]; ratio= 1.00 [-]; P_amb= 0.51 [bar]; alfa_M= 0.05 [-]; T_inf= 30.00 [°C]; surfactant= 100 [%]   |   NH3 production:  45055913634628550316238218647661899164384476905042190002667577729385069642362322638289715734511380662974671249494507520.0 [MJ/kg] (best:  1000000000000000019884624838656.0 [MJ/kg])                                                  
       such that in the machine, t + h = t on the next step  
       (h = step size). solver will continue anyway  
      in above,  r1 =  0.2304484397784D-03   r2 =  0.1209345117648D-19
 lsoda--  warning..internal t (=r1) and h (=r2) are  
       such that in the machine, t + h = t on the next step  
       (h = step size). solver will continue anyway  
      in above,  r1 =  0.2304484397784D-03   r2 =  0.1209345117648D-19
 lsoda--  warning..internal t (=r1) and h (=r2) are  
       such that in the machine, t + h = t on the next step  
       (h = st

/home/yoda/.local/lib/python3.10/site-packages/scipy/integrate/_ode.py:1348: UserWarning: lsoda: Excess accuracy requested (tolerances too small).
  warnings.warn('{:s}: {:s}'.format(self.__class__.__name__,


 lsoda--  at t (=r1), too much accuracy requested    
       for precision of machine..  see tolsf (=r2)   
      in above,  r1 =  0.1121795811115D-03   r2 =                  NaN


/home/yoda/.local/lib/python3.10/site-packages/scipy/integrate/_ode.py:1348: UserWarning: lsoda: Excess accuracy requested (tolerances too small).
  warnings.warn('{:s}: {:s}'.format(self.__class__.__name__,


 lsoda--  at t (=r1), too much accuracy requested    
       for precision of machine..  see tolsf (=r2)   
      in above,  r1 =  0.1102545784575D-03   r2 =                  NaN
 lsoda--  warning..internal t (=r1) and h (=r2) are   runtime:  0.74 [s]   |   R_E= 1.00 [um]; ratio= 1.00 [-]; P_amb= 0.51 [bar]; alfa_M= 0.05 [-]; T_inf= 30.00 [°C]; surfactant= 100 [%]   |   NH3 production:  141966448190521913046880208753964420634926598637942172240653328179751856501952926242117497528406041288125365486633353216.0 [MJ/kg] (best:  1000000000000000019884624838656.0 [MJ/kg])                                                 
       such that in the machine, t + h = t on the next step  
       (h = step size). solver will continue anyway  
      in above,  r1 =  0.1182986981293D-02   r2 =  0.4190182176019D-19
 lsoda--  warning..internal t (=r1) and h (=r2) are  
       such that in the machine, t + h = t on the next step  
       (h = step size). solver will continue anyway  
      in above,  r1 = 

...

capi_return is NULL
Call-back cb_f_in_lsoda__user__routines failed.


capi_return is NULL
Call-back cb_f_in_lsoda__user__routines failed.


capi_return is NULL
Call-back cb_f_in_lsoda__user__routines failed.


capi_return is NULL
Call-back cb_f_in_lsoda__user__routines failed.


index: 12599/12600,   error_code:    0,   steps: 12795,   runtime:  3.09 [s]   |   R_E= 25.00 [um]; ratio= 1.00 [-]; P_amb= 5.07 [bar]; alfa_M= 0.35 [-]; T_inf= 30.00 [°C]; surfactant= 100 [%]   |   NH3 production:  1000000000000000019884624838656.0 [MJ/kg] (best:  835.3 [MJ/kg])                                                        g])                                                     

DONE
total time:  5 hours  15 mins
             18920.41 [s]   ( 1.50 [s/run])
